In [ ]:
# %%capture supresses output from pip install
%%capture
!pip install chart_studio
!pip install yfinance
!pip install cufflinks

In [ ]:
import pandas as pd
import cufflinks as cf
import numpy as np
import yfinance as yf
import plotly.graph_objects as go
from plotly.offline import iplot, init_notebook_mode
from plotly.subplots import make_subplots
import plotly.io as pio 
pio.renderers.default = 'colab'
import warnings
from datetime import date, timedelta
# import chart_studio; chart_studio.tools.set_credentials_file(username='username', api_key='apikey') # https://plotly.com/python/getting-started-with-chart-studio/
from itertools import cycle

Multiple Tickers





In [ ]:
# Get Multiple Ticker Data. Methods add_vol_color and add_smas are now built into method multi_ticker_data as functions.
class MultiTickerData():
  def __init__(self, symbols, start_date, interval='1d', sma_list=[7, 21, 50, 200], ema_list=[7, 21, 50, 200], vma_list=[50], end_date=(date.today() + timedelta(days=1))):
    self.symbols = symbols
    self.start_date = start_date
    self.end_date = end_date
    self.interval = interval
    self.sma_list = sma_list
    self.ema_list = ema_list
    self.vma_list = vma_list
    self.pv_data = self.get_ticker_data()

  def get_ticker_data(self):
    multi_ticker_data = []
    
    # Function add_vol_color: Use lambda function to create a VolumeColor column that will return 'green' if close > open, 'red' if close < open. For coloring volume bar chart.
    def add_vol_color(rawdata):
      def volume_color(open, close):
        if close > open:
          return 'mediumseagreen'
        else:
          return 'tomato'
      rawdata['VolumeColor'] = rawdata.apply(lambda x: volume_color(x['Open'], x['Close']), axis=1)
      return rawdata
    
    # Function add_smas: specify sma_list ([7, 21, 50, 200] is default for a 1 day interval) and add sma to price volume dataframe as individual columns.
    # sma_list = [1, 5, 10] if doing weeks
    def add_smas(rawdata):
      #List of SMAs - determined by interval, ie sma_list[0] = 50, interval = "1d" means we are calculating the 50-day SMA.
      for s in self.sma_list:
        # Create new column in price volume data frame based of sma value
        rawdata['{unit}-{interval}-SMA'.format(unit=s, interval=self.interval)] = rawdata['Close'].rolling(window = s).mean()
      return rawdata
    
    # Function add_emas: specify ema_list ([7, 21, 50, 200] is default for a 1 day interval) and add ema to price volume dataframe as individual columns.
    # ema_list = [1, 5, 10] if doing weeks
    def add_emas(rawdata):
      #List of EMAs - determined by interval, ie ema_list[0] = 50, interval = "1d" means we are calculating the 50-day EMA.
      for e in self.ema_list:
        # Create new column in price volume data frame based of ema value
        rawdata['{unit}-{interval}-EMA'.format(unit=e, interval=self.interval)] = rawdata['Close'].ewm(span = e, adjust=False).mean()
      return rawdata

    # Function add_vmas: specify vma_list and add vma to price volume dataframe as individual column
    def add_vmas(rawdata):
      for v in self.vma_list:
        rawdata[f"{v}-{self.interval}-VMA"] = rawdata['Volume'].rolling(window=v).mean()
      return rawdata

    # Get Price Volume Data from yf
    for single_ticker in self.symbols:
      rawdata = yf.download(single_ticker, start=self.start_date, end=self.end_date, interval=self.interval)
      # Create column with ticker symbol
      rawdata['ticker'] = single_ticker
      # Remove column with ticker
      ticker_column = rawdata.pop('ticker')
      # Move ticker column back to the front
      rawdata.insert(0,'ticker',ticker_column)
      # Call functions defined above. A function call is used here instead of a method to scale to multiple tickers.
      rawdata = add_vol_color(rawdata) 
      rawdata = add_smas(rawdata)
      rawdata = add_vmas(rawdata)
      rawdata = add_emas(rawdata)

      multi_ticker_data.append(rawdata)
    multi_ticker_data = pd.concat(multi_ticker_data)
    return multi_ticker_data


  # Method plot_candlestick. Creates a plotly of all tickers that can be individually chosen via dropdown.
  def plot_candlestick(self, use_emas = False):
      
      fig = make_subplots(rows=2, cols=1, shared_xaxes=True, 
                      vertical_spacing=0.05, #subplot_titles=('Price', 'Volume'), 
                      row_width=[0.2, 0.7])

      for ticker in self.symbols:
          single_ticker = self.pv_data[self.pv_data["ticker"] == ticker]
          trace1 =  go.Candlestick(x=single_ticker.index,
                            open=single_ticker["Open"],
                            high=single_ticker["High"],
                            low=single_ticker["Low"],
                            close=single_ticker["Close"],
                            name='Candlestick')
          # Remove rangeslider default for Plotly Candlestick
          fig.update(layout_xaxis_rangeslider_visible=False)
          fig.append_trace(trace1,1,1)
          # Bar trace for volumes on 2nd row without legend
          trace2 = go.Bar(x=single_ticker.index, y=single_ticker['Volume'], marker={'color':single_ticker['VolumeColor']}, name='Volume', showlegend=False)
          fig.append_trace(trace2,2,1)

          # Plot EMAs instead of SMAs
          if use_emas is True:

            # Add Multiple EMAs based off of EMA list. Iterate through colors of blue if more than 1 ema is used
            ema_color_cycle = cycle(['skyblue','deepskyblue','dodgerblue', 'cadetblue', 'royalblue'])
            for s in self.ema_list:
              current_ema = '{unit}-{interval}-EMA'.format(unit=s, interval=self.interval) 
              trace3 = go.Scatter(
                x=single_ticker.index,
                y=single_ticker[current_ema],
                name=current_ema,
                line=dict(color=next(ema_color_cycle), width=1)
                )
              fig.append_trace(trace3,1,1)

          else:
            # Add Multiple SMAs based off of SMA list. Iterate through colors of blue if more than 1 sma is used
            sma_color_cycle = cycle(['skyblue','deepskyblue','dodgerblue', 'cadetblue', 'royalblue'])
            for s in self.sma_list:
              current_sma = '{unit}-{interval}-SMA'.format(unit=s, interval=self.interval) 
              trace3 = go.Scatter(
                x=single_ticker.index,
                y=single_ticker[current_sma],
                name=current_sma,
                line=dict(color=next(sma_color_cycle), width=1)
                )
              fig.append_trace(trace3,1,1)


          # Add Average Volume to bottom row
          vma_color_cycle = cycle(['skyblue','deepskyblue','dodgerblue', 'cadetblue', 'royalblue'])
          for v in self.vma_list:
            current_vma = '{unit}-{interval}-VMA'.format(unit=v, interval=self.interval) 
            trace4 = go.Scatter(
              x=single_ticker.index,
              y=single_ticker[current_vma],
              name=current_vma,
              line=dict(color=next(vma_color_cycle), width=1,
                              dash='dot')
              )
            fig.append_trace(trace4,2,1)


      num_smas = len(self.sma_list)
      num_figures = len(fig.data)
      num_tickers = len(self.symbols)
      # # Figs / Ticker. 2 for Price and Volume, along with each SMA Curve.
      # print(num_figures / num_tickers
      #step = 2 + num_smas
      step = int(num_figures / num_tickers)

      # Initial Plotly Layout: turn all figures off except for the figures associated with first ticker
      for k in range(step, num_figures): 
          # Starting from step (the number of figs / ticker), turn the rest of the traces off.
          fig.update_traces(visible=False, selector = k)

      def create_layout_button(k, ticker):
          # Create a visibility array based on the total number of figures
          visibility= [False]*step*num_tickers

          # Turn on only the figures associated with a single ticker
          index1=k
          index2=k+step
          visibility[index1:index2] = [True] * (step) 
          
          return dict(label = ticker,
                      method = 'restyle',
                      args = [{'visible': visibility,
                              'title': ticker,
                              'showlegend': True}])    
      
      fig.update_layout(
          updatemenus=[go.layout.Updatemenu(
              active = 0,
              # Create Layout Button along with array of visibility. Index k skips every step in enumerate (enumerate usually does single increment)
              buttons = [create_layout_button(k*step, ticker) for k, ticker in enumerate(self.symbols)],
              )
          ],
          title="Adjusted Stock Price",
          yaxis_title="Price ($)",
          template="plotly_dark",
          # annotations=[
          # dict(text="Ticker:", showarrow=False,
          # x=0, y=1.085, xref='paper',yref='paper', align="left") # 
          # ]
          )

      fig.show()


In [ ]:
focus_list = ['NVDA', 'PANW', 'ALGM', 'NXT', 'XBI', 'MELI', 'AXON', 'MBLY', 'MDY', 'AEHR', 'META', 'ELF','ABNB', 'FTNT', 'ANET', 'WFRD', 'LSCC', 'ACLS', 'STNG', 'UAL', 'CDNS', 'SMCI', 'TOL', 'FSLR', 'AEHR']
tml_data = MultiTickerData(focus_list, "2020-01-01", sma_list=[7, 21, 50])
# print(test.ema_list)
# print(tml_data.pv_data.head(10))
tml_data.plot_candlestick(use_emas=True)
# tml_data.plot_candlestick(use_emas=False)

[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%********

In [ ]:
# Get Individual Ticker Data
class SingleTickerData():
  def __init__(self, symbol, start_date, interval='1d', end_date=date.today() + timedelta(days=1)):
    self.symbol = symbol
    self.start_date = start_date
    self.end_date = end_date
    self.interval = interval
    rawdata = yf.download(self.symbol, start=self.start_date, end=self.end_date, interval=self.interval)
    # Create column with ticker symbol
    rawdata['ticker'] = self.symbol
    # Remove column with ticker
    ticker = rawdata.pop('ticker')
    # Move ticker column back to the front
    rawdata.insert(0,'ticker',ticker)
    self.pv_data = rawdata
    
    self.add_vol_color()
    self.sma_list = None


  # Method add_vol_color: Use lambda function to create a VolumeColor column that will return 'green' if close > open, 'red' if close < open. For coloring volume bar chart.
  def add_vol_color(self):
    def volume_color(open, close):
      if close > open:
        return 'mediumseagreen'
      else:
        return 'tomato'
    self.pv_data['VolumeColor'] = self.pv_data.apply(lambda x: volume_color(x['Open'], x['Close']), axis=1)


  # Method add_smas: specify sma_list ([7, 21, 50, 200] is default for a 1 day interval) and add sma to price volume dataframe as individual columns.
  # sma_list = [1, 5, 10] if doing weeks
  def add_smas(self, sma_list = [7, 21, 50, 200]):
    #List of SMAs - determined by interval, ie sma_list[0] = 50, interval = "1d" means we are calculating the 50-day SMA.
    self.sma_list = sma_list
    for s in sma_list:
      # Create new column in price volume data frame based of sma value
      self.pv_data['{unit}-{interval}-SMA'.format(unit=s, interval=self.interval)] = self.pv_data['Close'].rolling(window = s).mean()


  # Method candlestick: Plot Price and Volume Chart along with smas for a Single Ticker using Plotly's Base Library
  def candlestick(self):
    if self.sma_list is None:
      print("Error with method candlestick. Add your SMAs first.")
    else:
      df = self.pv_data
      # Create subplots to have Price and Volume on same Chart and mention plot grid size
      fig = make_subplots(rows=2, cols=1, shared_xaxes=True, 
                    vertical_spacing=0.03, #subplot_titles=('Price', 'Volume'), 
                    row_width=[0.2, 0.7])
      fig.add_trace(
          go.Candlestick(x=df.index,
                          open=df["Open"],
                          high=df["High"],
                          low=df["Low"],
                          close=df["Close"],
                          name='candlestick'),
                          row=1,
                          col=1   
      )
      # Remove rangeslider default for Plotly Candlestick
      fig.update(layout_xaxis_rangeslider_visible=False)
      # Bar trace for volumes on 2nd row without legend
      fig.add_trace(go.Bar(x=df.index, y=df['Volume'], marker={'color':df['VolumeColor']}, showlegend=False), row=2, col=1)
      # Add Multiple SMAs based off of SMA list. Iterate through colors of blue if more than 1 sma is used
      sma_color_cycle = cycle(['skyblue','deepskyblue','dodgerblue', 'cadetblue', 'royalblue'])
      for s in self.sma_list:
        current_sma = '{unit}-{interval}-SMA'.format(unit=s, interval=self.interval)
        fig.add_trace(
          go.Scatter(
          x=df.index,
          y=df[current_sma],
          name=current_sma,
          marker_color= next(sma_color_cycle)
          )
        )

      fig.update_layout(
          title=f"{self.symbol}'s Adjusted Stock Price",
          yaxis_title="Price ($)",
          template="plotly_dark"
      )
      # Print Figure upon calling the method.
      fig.show()




In [ ]:
today = date.today() + timedelta(days=1)
end_date = today
ticker = SingleTickerData('AEHR', "2020-01-01")
ticker.add_smas()
ticker.candlestick()

